In [1]:
# webpage extraction with beautifulsoup
import urllib2
from bs4 import BeautifulSoup
import re

'''
import sys
reload(sys)
sys.setdefaultencoding("utf-8")
'''
#specify the url
manual = 'https://haynes.com/en-us/car-manuals/car-makes'

#Query the website and return the html to the variable 'page'
page = urllib2.urlopen(manual)

In [2]:
soup = BeautifulSoup(page, "lxml")

In [ ]:
print soup.prettify()

In [4]:
makes = soup.find_all("div", class_="item-list")[1]
links_makes = makes.find_all("div", class_ = "views-field views-field-nothing")

In [5]:
list_makes = []
prefix = "https://haynes.com"
for make in links_makes:
    list_makes.append(prefix + make.a["href"])    

In [6]:
#Query the website and return the html to the variable 'page'
list_models = []

for link in list_makes:
    page_temp = urllib2.urlopen(link)
    soup_temp = BeautifulSoup(page_temp, "lxml")
    model_temp = soup_temp.find_all("div", class_="item-list")[1]
    links_model = model_temp.find_all("li")
    for model in links_model:
        list_models.append(model.a["href"])


In [85]:

link = "https://haynes.com/en-us/chevroletgmc-camionetas-haynes-manual-de-reparaci-n-88-al-98-incluye-suburban-92-al-98-blazer-jimmy"
#page_temp = urllib2.urlopen(link)
#soup_temp = BeautifulSoup(page_temp, "lxml")
output = []
'''
description = soup_temp.find("div", class_ = "group-product-description field-group-div")
if description:
    description = description.text

table = soup_temp.find("div", class_ = "field field-name-field-product-table-of-contents field-type-text-long")
if table:
    table = table.text

print table
'''

extract_info(link, output)

the description is Product descriptionLos Manuales Haynes Explican Mejor:
Paso por paso de los cientos de procedimientos con fotografías para que sean más fáciles de seguir.
Escritos por manos que tienen experiencia…usando herramientas comunes.
Sección para los procedimientos de identificación y soluciones rápidas y fáciles de problemas.
Diagramas detallando los alambrados.
Diagnóstico en colores para las bujías.
With Haynes Spanish Manuals, you can do-it-yourself...from simple maintenance to basic repairs. Haynes writes every book based on a complete teardown of the vehicle. Haynes learns the best ways to do a job and that makes it quicker, easier and cheaper for you. Haynes books have clear instructions and hundreds of photographs that show each step. Whether you are a beginner or a pro, you can save big with Haynes! This manual is in Spanish.
What's covered: Chevrolet/GMC Camionetas Haynes Manual de Reparación: 88 al 98 incluye Suburban 92 al 98, Blazer & Jimmy (los modelos de tamañ

In [86]:
import csv
import pandas as pd
from numpy import array

output = array(output)
print type(output)
print [str(s).replace('...' , '') for s in output]

with open("test.csv", "w") as f:
    writer = csv.writer(f)
    writer.writerow(["title","price", "Format","decription", "table", "part_no", "dimensions", "pages","ISBN13", "ISBN10", "UPC", "publish_date", "language", "reviews"])
    writer.writerows(output)

<type 'numpy.ndarray'>
['[ \'Chevrolet/GMC Camionetas Haynes Manual de Reparaci\\xc3\\xb3n: 88 al 98 incluye Suburban 92 al 98, Blazer & Jimmy (los modelos de tama\\xc3\\xb1o Grande 92 al 94, & Tahoe y Yukon 95 al 98. Todos los motores de gasolina, de 2 y 4 tracciones. (edici\\xc3\\xb3n espa\\xc3\\xb1ola)\'\n \'$29.95\' \'Paperback\'\n "Product descriptionLos Manuales Haynes Explican Mejor:\\nPaso por paso de los cientos de procedimientos con fotograf\\xc3\\xadas para que sean m\\xc3\\xa1s f\\xc3\\xa1ciles de seguir.\\nEscritos por manos que tienen experiencia\\xe2\\x80\\xa6usando herramientas comunes.\\nSecci\\xc3\\xb3n para los procedimientos de identificaci\\xc3\\xb3n y soluciones r\\xc3\\xa1pidas y f\\xc3\\xa1ciles de problemas.\\nDiagramas detallando los alambrados.\\nDiagn\\xc3\\xb3stico en colores para las buj\\xc3\\xadas.\\nWith Haynes Spanish Manuals, you can do-it-yourselffrom simple maintenance to basic repairs. Haynes writes every book based on a complete teardown of the ve

In [87]:
def extract_info(link, result):
    page_1 = urllib2.urlopen(link)
    soup_1 = BeautifulSoup(page_1, "lxml")
    title = soup_1.find("h1", class_="product-title").get_text()
    title = title.encode("utf-8")
    
    #print "the title is " + title
    
    price = soup_1.find("span", class_="price-amount commerce-price-savings-formatter-price").get_text()
    if price:
        price = price.encode("utf-8")
            
    body = soup_1.find_all("div", class_="field-item even")
    
    Format = body[2].text.replace('\n', '')
    if Format:
        Format = Format.encode("utf-8")
    
    #decription = body[4].get_text() + body[5].get_text()+ body[6].get_text() + body[7].get_text()
    description = soup_1.find("div", class_ = "group-product-description field-group-div")
    if description:
        description = description.text
        print "the description is " + description
        description = description.encode("utf-8")

    table = soup_1.find("div", class_ = "field field-name-field-product-table-of-contents field-type-text-long")
    if table:
        table = table.text
        table = table.encode("utf-8")
        
    #table = body[8].get_text()
    #table = soup_1.find("div", class_ = "field field-name-field-product-table-of-contents field-type-text-long")
    #if table:
    #   table = table.text
    #  table = table.encode("utf-8","ignore")
    #part_no = soup_1.findAll('div', text = re.compile('Part number'), attrs = {'class' : 'field-item even'})
    part = soup_1.find("div", string = re.compile("Part number"))
    if part:
        part = part.nextSibling.text
        part = part.encode("utf-8")
    
    dimensions = soup_1.find("div", string = re.compile("Dimensions"))
    if dimensions:
        dimensions = dimensions.nextSibling.text
        dimensions = dimensions.encode("utf-8")
        
    pages = soup_1.find("div", string = re.compile("# of pages"))
    if pages:
        pages = pages.nextSibling.text
        pages = pages.encode("utf-8")
        
    ISBN13 = soup_1.find("div", string = re.compile("ISBN-13"))
    if ISBN13:
        ISBN13 = ISBN13.nextSibling.text
        ISBN13 = ISBN13.encode("utf-8")
        
    ISBN10 = soup_1.find("div", string = re.compile("ISBN-10"))
    if ISBN10:
        ISBN10 = ISBN10.nextSibling.text
        ISBN10 = ISBN10.encode("utf-8")
        
    UPC = soup_1.find("div", string = re.compile("UPC"))
    if UPC:
        UPC = UPC.nextSibling.text
        UPC = UPC.encode("utf-8")
        
    publish_date = soup_1.find("div", string = re.compile("Publication date"))
    if publish_date:
        publish_date = publish_date.nextSibling.text
        publish_date = publish_date.encode("utf-8")
        
    language = soup_1.find("div", string = re.compile("Language"))
    if language:
        language = language.nextSibling.text
        language = language.encode("utf-8")
    
    reviews = soup_1.find("iframe", class_ = "product-reviews-amazon")
    if reviews is not None:
        reviews = reviews["src"]
        reviews = reviews.encode("utf-8")
    
    result.append([title, price, Format,description, table, part, dimensions, pages,ISBN13, ISBN10, UPC, publish_date, language, reviews])
    #result.append([title, description])

In [88]:
import time
start = time.time()

result = []
for link in list_models:
    # 3 types of links
    # 1-result of a search, go to next level
    if "search?query" in link:
        page_temp = urllib2.urlopen(link)
        soup_temp = BeautifulSoup(page_temp, "lxml")
        model_temp = soup_temp.find_all("div", class_="product-teaser-title")[1]
        for item in model_temp:
            if item is not None:
                #print item
                link_temp = prefix + item["href"]
                extract_info(link_temp, result)
         
    # 2-need to go to next level by "more info"
    elif link[-1].isdigit():
        page_temp = urllib2.urlopen(link)
        soup_temp = BeautifulSoup(page_temp, "lxml")
        link_temp = soup_temp.find_all("div", class_="views-field views-field-view-node")
        for item in link_temp:
            link_1 = prefix + item.a["href"]
            extract_info(link_1, result)
    
    # 3-final page
    else:
        extract_info(link, result)
        
end = time.time()
print(end - start)
'''
    page_temp = urllib2.urlopen(link)
    soup_temp = BeautifulSoup(page_temp)
    
    model_temp = soup_temp.find_all("div", class_="item-list")[1]
    links_model = model_temp.find_all("li")
    for model in links_model:
        list_models.append(model.a["href"])
'''

the description is Product descriptionComplete coverage for your Honda Civic & CR-V / Acura Integra for these models/years: Honda Civic (1996 thru 2000), Honda CR-V (1997 thru 2001), and Acura Integra (1994 thru 2000):  Routine Maintenance  Tune-up procedures  Engine repair  Cooling and heating  Air Conditioning  Fuel and exhaust  Emissions control  Ignition  Brakes  Suspension and steering  Electrical systems  Wiring diagrams
With a Haynes manual, you can do it yourself…from simple maintenance to basic repairs. Haynes writes every book based on a complete teardown of the vehicle. We learn the best ways to do a job and that makes it quicker, easier and cheaper for you. Our books have clear instructions and hundreds of photographs that show each step. Whether you’re a beginner or a pro, you can save big with Haynes! --Step-by-step procedures --Easy-to-follow photos --Complete troubleshooting section --Valuable short cuts  --Color spark plug diagnosis
What's covered: Honda Civic (1996-20

'\n    page_temp = urllib2.urlopen(link)\n    soup_temp = BeautifulSoup(page_temp)\n    \n    model_temp = soup_temp.find_all("div", class_="item-list")[1]\n    links_model = model_temp.find_all("li")\n    for model in links_model:\n        list_models.append(model.a["href"])\n'

In [14]:
result

[[u'Honda Civic (1996-2000), CR-V (1997-2001) & Acura Integra (1994-2000) Haynes Repair Manual',
  u'$29.95',
  u'Paperback',
  "Product descriptionComplete coverage for your Honda Civic & CR-V / Acura Integra for these models/years: Honda Civic (1996 thru 2000), Honda CR-V (1997 thru 2001), and Acura Integra (1994 thru 2000):  Routine Maintenance  Tune-up procedures  Engine repair  Cooling and heating  Air Conditioning  Fuel and exhaust  Emissions control  Ignition  Brakes  Suspension and steering  Electrical systems  Wiring diagrams\nWith a Haynes manual, you can do it yourself\xe2\x80\xa6from simple maintenance to basic repairs. Haynes writes every book based on a complete teardown of the vehicle. We learn the best ways to do a job and that makes it quicker, easier and cheaper for you. Our books have clear instructions and hundreds of photographs that show each step. Whether you\xe2\x80\x99re a beginner or a pro, you can save big with Haynes! --Step-by-step procedures --Easy-to-foll

In [ ]:
#result_update = [[str(x).replace('...', '') for x in l] for l in result]
#result_update = [[if x x.replace('...', '') else x for x in i] for i in result]
'''
list_result = "-----".join(map(str, result))
result_update = list_result.replace("...", "")

print result_update
'''
'''
for i in result:
    for j in i:
        if j:
            j = j.replace("...", "")
'''

In [ ]:
#result_final = result_update.split("-----")
#result_temp = [x.split(""",""") for x in result_final]

In [89]:
import json

with open("final.json", "w") as writeJSON:
    json.dump(result, writeJSON)

In [93]:
import csv
#import pandas as pd
#from numpy import array

#output = array(result)
#print type(output)
#print [str(s).replace('...' , '') for s in output]

with open("another1.csv", "wb") as f:
    writer = csv.writer(f)
    writer.writerow(["title","price", "Format","decription", "table", "part_no", "dimensions", "pages","ISBN13", "ISBN10", "UPC", "publish_date", "language", "reviews"])
    writer.writerows(result)

'''
with open("final.csv", "w") as toWrite:
    writer = csv.writer(toWrite, delimiter=",")
    writer.writerow(["title","price", "Format","decription", "table", "part_no", "dimensions", "pages","ISBN13", "ISBN10", "UPC", "publish_date", "language", "reviews"])
    for a in output:
        writer.writerow(a)
'''

'\nwith open("final.csv", "w") as toWrite:\n    writer = csv.writer(toWrite, delimiter=",")\n    writer.writerow(["title","price", "Format","decription", "table", "part_no", "dimensions", "pages","ISBN13", "ISBN10", "UPC", "publish_date", "language", "reviews"])\n    for a in output:\n        writer.writerow(a)\n'